In [1]:
import matplotlib.pyplot as plt
import numpy as np
from qiskit import QuantumCircuit, QuantumRegister
from qiskit.circuit import ParameterVector
from qiskit.quantum_info import SparsePauliOp
import math
from qiskit.circuit.library import RYGate
import ttg


In [2]:
def scale_states_between_zero_pi(data):

  x_min = np.min(data)
  x_max = np.max(data)

  for index, x in enumerate(data):
    x_scaled = (( x - x_min) / (x_max - x_min)) * np.pi
    data[index] = x_scaled

  return data


In [3]:
from math import log2
def tree_hybrid_amplitude_encoding(data):

  data = scale_states_between_zero_pi(data)

  q = QuantumRegister(math.ceil(log2(len(data))))

  qc = QuantumCircuit(q)

  ## on the index of the qubit we determine how many gate we need
  ## for we need to loop on the quantum circuit

  ## index of training data
  index_x = 0

  for qubit in q:

    n_gate = 2 ** qubit._index

    ## controlled gates based on the n_gate which is 4 controlled gates
    ## with different open and closed gates

    c_q = q[0:qubit._index]

    ## generate truth table based on the number of control qubits and loop on them that if the qubit is 0 we put not gate before and after the toffoli gate

    if len(c_q) > 0:

      n = [str(i) for i in range(0, len(c_q))]

      truth_table = ttg.Truths(n, ascending=True)

      truth_table = truth_table.as_pandas.to_dict('index')

      for index in range(n_gate):


        row = truth_table[index + 1]


        for key in row:

          value = row[key]

          if int(value) == 0:

            qc.x(c_q[int(key)])

        qc.mcry(data[index_x], c_q, qubit, [], mode='noancilla')

        for key in row:

          value = row[key]

          if int(value) == 0:

            qc.x(c_q[int(key)])

        index_x += 1

        qc.barrier()

    else:

      qc.ry(data[index_x], qubit)

      index_x += 1


  return qc

In [4]:
circuit = tree_hybrid_amplitude_encoding([ 1, 2,  3, 4, 5, 6, 7, 8, 10, 20,  23, 14, 5, 16, 27, 18])
circuit

In [5]:
def conv_circuit(params):
    target = QuantumCircuit(2)
    target.rz(-np.pi /2, 1)
    target.cx(1, 0)
    target.rz(params[0], 0)
    target.ry(params[1], 1)
    target.cx(0, 1)
    target.ry(params[2], 1)
    target.cx(1, 0)
    target.rz(np.pi / 2, 0)
    return target

In [6]:
def conv_layer(num_qubits, param_prefix):
    qc = QuantumCircuit(num_qubits, name="Convolutional Layer")
    qubits = list(range(num_qubits))
    param_index = 0
    params = ParameterVector(param_prefix, length=num_qubits * 3)
    for q1, q2 in zip(qubits[0::2], qubits[1::2]):
        qc = qc.compose(conv_circuit(params[param_index : (param_index + 3)]), [q1, q2])
        qc.barrier()
        param_index += 3
    for q1, q2 in zip(qubits[1::2], qubits[2::2] + [0]):
        qc = qc.compose(conv_circuit(params[param_index : (param_index + 3)]), [q1, q2])
        qc.barrier()
        param_index += 3

    qc_inst = qc.to_instruction()

    qc = QuantumCircuit(num_qubits)
    qc.append(qc_inst, qubits)

    return qc


In [7]:
def pool_circuit(params):
    target = QuantumCircuit(2)
    target.rz(-np.pi / 2, 1)
    target.cx(1, 0)
    target.rz(params[0], 0)
    target.ry(params[1], 1)
    target.cx(0, 1)
    target.ry(params[2], 1)

    return target

In [8]:
def pool_layer(sources, sinks, param_prefix):
    num_qubits = len(sources) + len(sinks)
    qc = QuantumCircuit(num_qubits, name="Pooling Layer")
    param_index = 0
    params = ParameterVector(param_prefix, length=num_qubits // 2 * 3)
    for source, sink in zip(sources, sinks):
        qc = qc.compose(pool_circuit(params[param_index : (param_index + 3)]), [source, sink])
        qc.barrier()
        param_index += 3

    qc_inst = qc.to_instruction()

    qc = QuantumCircuit(num_qubits)
    qc.append(qc_inst, range(num_qubits))
    return qc

In [12]:
sources = [0, 1]
sinks = [2, 3]
circuit = tree_hybrid_amplitude_encoding([ 1, 2,  3, 4, 5, 6, 7, 8, 10, 20,  23, 14, 5, 16, 27, 18])
circuit = circuit.compose(conv_layer(4, "c"))
circuit = circuit.compose(pool_layer(sources, sinks, "p"))

In [11]:
feature_map = tree_hybrid_amplitude_encoding([ i for i in range(0,256)])

ansatz = QuantumCircuit(8, name="Ansatz")

# First Convolutional Layer
ansatz.compose(conv_layer(8, "c1"), list(range(8)), inplace=True)

# First Pooling Layer
ansatz.compose(pool_layer([0, 1, 2, 3], [4, 5, 6, 7], "p1"), list(range(8)), inplace=True)

# Second Convolutional Layer
ansatz.compose(conv_layer(4, "c2"), list(range(4, 8)), inplace=True)

# Second Pooling Layer
ansatz.compose(pool_layer([0, 1], [2, 3], "p2"), list(range(4, 8)), inplace=True)

# Third Convolutional Layer
ansatz.compose(conv_layer(2, "c3"), list(range(6, 8)), inplace=True)

# Third Pooling Layer
ansatz.compose(pool_layer([0], [1], "p3"), list(range(6, 8)), inplace=True)

# Combining the feature map and ansatz
circuit = QuantumCircuit(8)
circuit.compose(feature_map, range(8), inplace=True)
circuit.compose(ansatz, range(8), inplace=True)

observable = SparsePauliOp.from_list([("Z" + "I" * 7, 1)])

circuit.draw('mpl')